## 1. Import Dependencies

In [1]:
#import gym stuff
import gym 
from gym import Env
from gym.spaces import Discrete, Box, Dict, Tuple, MultiBinary, MultiDiscrete 
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.callbacks import EvalCallback, StopTrainingOnRewardThreshold

#import helpers
import numpy as np
import random
import os
import pandas as pd

#import stable_baseline stuff
from stable_baselines3 import PPO, DQN
from stable_baselines3.common.vec_env import VecFrameStack
from stable_baselines3.common.evaluation import evaluate_policy

## 2. Creat Env

In [2]:
class CustomEnv(Env):
    def __init__(self, data_path = "Data_test\data_demo.csv"):
        
        self.action_space = Discrete(141)
        self.observation_space = Discrete(242, start=100)
        #self.observation_space = Box(low=100, high=161, shape=(1,), dtype=int)
        
        data = pd.read_csv("Data_test\data_demo.csv")
        #self.data_request = data.request
        #self.data_response = data.response
        #self.data_lable = data.lable
        self.data_request_list = data.request.to_list()
        self.data_general_request_list = data.general_request.to_list()
        self.data_general_unique_list = data.general_unique.tolist()
        self.data_response_list = data.response_simple.to_list()
        self.data_lable_list = data.lable.to_list()
        self.data_value_list = data._value_.to_list()
        self.data_key_request_list = data.key_request.to_list()
                 
        #Lấy index các dạng tổng quát
        self.lable_exploit_list = [self.data_value_list[index] for index, label in enumerate(self.data_lable_list) if label == 'exploit']
        self.lable_upload_list = [self.data_value_list[index] for index, label in enumerate(self.data_lable_list) if label == 'upload']
        self.lable_end_list = [self.data_value_list[index] for index, label in enumerate(self.data_lable_list) if label == 'end']             

        self.general_upload = [index for index, general in enumerate(self.data_general_unique_list) if general == 'MixString-MixStringMixString-MixStringname=PureStringfilename=PureString.php']
        self.general_end = [index for index, general in enumerate(self.data_general_unique_list) if general == 'MixString']

        self.general_cmdinj_1_collect = [index for index, general in enumerate(self.data_general_unique_list) if general =="ip=Number.Number.Number.Number%HexString%HexStringMixString&Submit=PureString"]
        self.general_cmdinj_2_collect = [index for index, general in enumerate(self.data_general_unique_list) if general =="ip=Number.Number.Number.Number%HexString%HexStringMixString-MixString&Submit=PureString"]
        self.general_cmdinj_3_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="ip=Number.Number.Number.Number%HexString%HexStringMixString-MixString%HexStringMixString%HexStringMixStringNumber.Number.Number.NumberNumber&Submit=PureString"]
        self.general_cmdinj_4_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="ip=Number.Number.Number.Number%HexString%HexStringMixString-MixString%HexString%HexString%HexStringMixString%HexStringMixString%HexStringNumber.Number.Number.Number%HexStringNumberNumber%HexString%HexStringNumber&Submit=PureString"]
        
        self.general_sql_1_collect = [index for index, general in enumerate(self.data_general_unique_list) if general =="?id=%HexStringNumber&Submit=PureString"]
        self.general_sql_2_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?id=%HexString%HexStringNumberMixString%HexStringNumber%HexString%HexString%HexStringNumber&Submit=PureString"]
        self.general_sql_3_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?id=%HexStringNumber%HexStringMixStringMixStringMixString%HexStringMixStringMixStringMixString%HexString&Submit=PureString"]
        self.general_sql_4_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="id=NumberMixStringNumber%HexStringNumber%HexString&Submit=PureString"]
        self.general_sql_5_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="id=%HexStringNumber%HexStringMixStringMixStringMixString%HexStringMixStringMixStringMixString%HexString&Submit=PureString"]
        self.general_sql_6_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?id=Number%HexStringMixStringMixString%HexStringNumber%HexString%HexString&Submit=PureString"]
        self.general_sql_7_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="id=NumberMixStringMixString%HexStringNumber%HexString%HexString&Submit=PureString"]
        
        
        self.general_xss_1_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?default=PureString%HexStringMixString%HexStringMixString(%HexStringMixString%HexStringMixString%HexStringMixString%HexStringNumber)%HexString/PathString%HexString"]
        self.general_xss_2_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?default=PureString%HexString/PathString%HexString%HexString/PathString%HexString%HexStringMixString%HexStringsrc=%HexStringMixString%HexString%HexStringonerror=%HexStringMixString(%HexStringNumberMixString.MixString%HexString)%HexString%HexString"]
        self.general_xss_3_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?name=%HexStringMixString%HexStringMixString%HexStringNumberMixString.MixString%HexString%HexString%HexString%HexStringMixString%HexString"]
        self.general_xss_4_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?name=%HexStringMixStringMixString%HexStringMixStringMixString%HexStringMixString%HexStringNumberMixString.MixString%HexString%HexString"]
        self.general_xss_5_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="txtName=PureString&mtxMessage=%HexStringMixString%HexStringMixString%HexStringNumberMixString.MixString%HexString%HexString%HexString%HexStringMixString%HexString&btnSign=PureStringMixString"]
        self.general_xss_6_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="txtName=%HexStringMixString%HexStringMixString%HexStringNumberMixString.MixString%HexString%HexString%HexString%HexStringMixString%HexString&mtxMessage=PureString&btnSign=PureStringMixString"]
        self.general_xss_7_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="txtName=%HexStringMixStringMixString%HexStringMixStringMixString%HexStringMixString%HexStringNumberMixString.MixString%HexString%HexString&mtxMessage=PureString&btnSign=PureStringMixString"]
        
        self.general_csrf_1_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?password_new=NumberPureString&password_conf=PureString&Change=PureString"]
        
        self.general_path_raversal_1_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?page=/PathString/PathString/PathString/PathString/PathString/PathString/PathString/PathString"]
        self.general_path_raversal_2_exploit = [index for index, general in enumerate(self.data_general_unique_list) if general =="?page=PureString.php%HexString/PathString/PathString/PathString/PathString/PathString/PathString/PathString/PathString"]                       
        
        
        # Initialize state
        self.lable_collect_list = [self.data_value_list[index] for index, label in enumerate(self.data_lable_list) if label == 'collect']
        self.state = np.random.choice(self.lable_collect_list)
        
        # Set shower length
        self.shower_length = 10
        
    def step(self, action):
        self.total_reward = 0
        self.shower_length -= 1 
        # Calculate reward
        if self.state in self.lable_collect_list:
            if action in self.general_cmdinj_1_collect and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 0
            elif action in self.general_cmdinj_2_collect and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 0
            elif action in self.general_sql_1_collect and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 0
            else:
                reward = -1
                
        elif self.state in self.lable_exploit_list:
            if action in self.general_cmdinj_3_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_cmdinj_4_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_sql_2_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_sql_3_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_sql_4_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_sql_5_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_sql_6_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_sql_7_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            
            elif action in self.general_xss_1_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_xss_2_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_xss_3_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_xss_4_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_xss_5_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_xss_6_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_xss_7_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
                
            elif action in self.general_csrf_1_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
                
            elif action in self.general_path_raversal_1_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            elif action in self.general_path_raversal_2_exploit and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 1
            else:
                reward = -1
            
            
        elif self.state in self.lable_upload_list:
            if action in self.general_upload and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
                reward = 5
            else:
                reward = -1
        elif self.state in self.lable_end_list and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
            if self.total_reward > 0:
                reward = 0
            else:
                reward = -1
        elif self.state in self.lable_end_list and self.data_key_request_list[action] == self.data_key_request_list[self.data_value_list.index(self.state)]:
            if self.total_reward <= 0:
                reward = -1
        else:
            reward = -1        
            
       
            
        self.total_reward += reward
            
       
        # Check if shower is done
        if self.shower_length <= 0: 
            done = True
        else:
            done = False
        
        if done:
            self.state = np.random.choice(self.lable_collect_list)
        else:
            self.state = np.random.choice(self.data_value_list)
        
        # Set placeholder for info
        info = {}
        
        # Return step information
        return self.state, reward, done, info

    
    def reset(self):
        # Reset shower temperature
        self.state = np.random.choice(self.lable_collect_list)
        # Reset shower time
        self.shower_length = 10
        return self.state

In [3]:
env = CustomEnv()

In [4]:
env.state

157

In [5]:
env.data_key_request_list[env.data_value_list.index(env.state)]

'1'

## 3. Test Environment

In [6]:
# Test the environment

episodes = 5
for episode in range(1, episodes + 1):
    state = env.reset()
    print(f"Current State {state}: {env.data_request_list[env.data_value_list.index(state)]}")
    done = False
    total_reward = 0

    print(f"================== Episode {episode} ===================")

    while not done:
        #print(f"Next State: {env.cmd_list[next_state]}")
        #print(f"Current State: {state}")
        

        # Take a random action
        action = env.action_space.sample()
        print(f"Selected Action {action}:\n{env.data_response_list[action]}")
        #print(f"Selected Action: {action}")

        # Step forward in the environment
        next_state, reward, done, _ = env.step(action)
        
        print(f"\nLength: {env.shower_length}")
        print(f"Reward: {reward} \n")
        total_reward += reward
        
        print(f"Next State {next_state}: {env.data_request_list[env.data_value_list.index(next_state)]}")

    print(f"Total Reward for Episode {episode}: {total_reward}\n\n")


Current State 147: ip=127.0.0.1+%7Chostname&Submit=Submit
================== Episode 1 ===================
Selected Action 54:
PING 127.0.0.1 (127.0.0.1): 56 data bytes
64 bytes from 127.0.0.1: icmp_seq=0 ttl=127 time=40.488 ms
64 bytes from 127.0.0.1: icmp_seq=1 ttl=127 time=38.966 ms
64 bytes from 127.0.0.1: icmp_seq=2 ttl=127 time=46.680 ms
64 bytes from 127.0.0.1: icmp_seq=3 ttl=127 time=37.922 ms
--- 127.0.0.1 ping statistics ---
4 packets transmitted, 4 packets received, 0% packet loss
round-trip min/avg/max/stddev = 37.922/41.014/46.680/3.396 ms

Length: 9
Reward: -1 

Next State 184: id=0%27+OR+sleep%283%29&Submit=Submit
Selected Action 68:
ID: 0 OR 0=0#
First name: admin
Surname: admin
ID: 0 OR 0=0#
First name: Gordon
Surname: Brown
ID: 0 OR 0=0#
First name: Hack
Surname: Me
ID: 0 OR 0=0#
First name: Pablo
Surname: Picasso
ID: 0 OR 0=0#
First name: Bob
Surname: Smith

Length: 8
Reward: -1 

Next State 215: txtName=uit&mtxMessage=%3Cscript%3Ealert%28%22you+been+hacked%21%22%29%

## 4. Vectorise Environment and Train Model

In [7]:
log_path = os.path.join('Training', 'Logs')

In [8]:
log_path

'Training\\Logs'

In [9]:
env = DummyVecEnv([lambda: env])
model = DQN('MlpPolicy', env, verbose = 1, tensorboard_log = log_path)

C:\Users\Asus\anaconda3\Lib\site-packages\stable_baselines3\common\vec_env\patch_gym.py:49: UserWarning: You provided an OpenAI Gym environment. We strongly recommend transitioning to Gymnasium environments. Stable-Baselines3 is automatically wrapping your environments in a compatibility layer, which could potentially cause issues.
  warnings.warn(
C:\Users\Asus\anaconda3\Lib\site-packages\torch\cuda\__init__.py:138: UserWarning: CUDA initialization: The NVIDIA driver on your system is too old (found version 11060). Please update your GPU driver by downloading and installing a new version from the URL: http://www.nvidia.com/Download/index.aspx Alternatively, go to: https://pytorch.org to install a PyTorch version that has been compiled with your version of the CUDA driver. (Triggered internally at ..\c10\cuda\CUDAFunctions.cpp:108.)
  return torch._C._cuda_getDeviceCount() > 0


Using cpu device


In [10]:
save_path = os.path.join('Training', 'Saved Models')

In [97]:
eval_callback = EvalCallback(env,
                            #callback_on_new_best=stop_callback,
                            eval_freq=100000,
                            best_model_save_path=save_path,
                            verbose= 1,
                            )

In [98]:
model.learn(total_timesteps=500000, callback=eval_callback)

Logging to Training\Logs\DQN_149
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.999    |
| time/               |          |
|    episodes         | 4        |
|    fps              | 2494     |
|    time_elapsed     | 0        |
|    total_timesteps  | 40       |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.998    |
| time/               |          |
|    episodes         | 8        |
|    fps              | 3364     |
|    time_elapsed     | 0        |
|    total_timesteps  | 80       |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.998    |
| time/               |          |
|    episodes         | 12       |
|    fps              | 4011     |
|    time_elapsed     | 0        |
|    total_timesteps  | 120      |
----------------------------------
----------------------

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.979    |
| time/               |          |
|    episodes         | 108      |
|    fps              | 5741     |
|    time_elapsed     | 0        |
|    total_timesteps  | 1080     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.979    |
| time/               |          |
|    episodes         | 112      |
|    fps              | 5764     |
|    time_elapsed     | 0        |
|    total_timesteps  | 1120     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.978    |
| time/               |          |
|    episodes         | 116      |
|    fps              | 5785     |
|    time_elapsed     | 0        |
|    total_timesteps  | 1160     |
----------------------------------
----------------------------------
| rollout/          

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.959    |
| time/               |          |
|    episodes         | 216      |
|    fps              | 6005     |
|    time_elapsed     | 0        |
|    total_timesteps  | 2160     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.958    |
| time/               |          |
|    episodes         | 220      |
|    fps              | 5997     |
|    time_elapsed     | 0        |
|    total_timesteps  | 2200     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.957    |
| time/               |          |
|    episodes         | 224      |
|    fps              | 6014     |
|    time_elapsed     | 0        |
|    total_timesteps  | 2240     |
----------------------------------
----------------------------------
| rollout/          

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.938    |
| time/               |          |
|    episodes         | 324      |
|    fps              | 6122     |
|    time_elapsed     | 0        |
|    total_timesteps  | 3240     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.938    |
| time/               |          |
|    episodes         | 328      |
|    fps              | 6121     |
|    time_elapsed     | 0        |
|    total_timesteps  | 3280     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.937    |
| time/               |          |
|    episodes         | 332      |
|    fps              | 6121     |
|    time_elapsed     | 0        |
|    total_timesteps  | 3320     |
----------------------------------
----------------------------------
| rollout/          

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.918    |
| time/               |          |
|    episodes         | 432      |
|    fps              | 6154     |
|    time_elapsed     | 0        |
|    total_timesteps  | 4320     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.917    |
| time/               |          |
|    episodes         | 436      |
|    fps              | 6148     |
|    time_elapsed     | 0        |
|    total_timesteps  | 4360     |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.916    |
| time/               |          |
|    episodes         | 440      |
|    fps              | 6151     |
|    time_elapsed     | 0        |
|    total_timesteps  | 4400     |
----------------------------------
----------------------------------
| rollout/          

...

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49672    |
|    fps              | 589      |
|    time_elapsed     | 842      |
|    total_timesteps  | 496720   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 1.77     |
|    n_updates        | 111679   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49676    |
|    fps              | 589      |
|    time_elapsed     | 842      |
|    total_timesteps  | 496760   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 1.84     |
|    n_updates        | 111689   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rat

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49748    |
|    fps              | 589      |
|    time_elapsed     | 844      |
|    total_timesteps  | 497480   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 1.2      |
|    n_updates        | 111869   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49752    |
|    fps              | 589      |
|    time_elapsed     | 844      |
|    total_timesteps  | 497520   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 1.79     |
|    n_updates        | 111879   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rat

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49824    |
|    fps              | 589      |
|    time_elapsed     | 845      |
|    total_timesteps  | 498240   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.616    |
|    n_updates        | 112059   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49828    |
|    fps              | 589      |
|    time_elapsed     | 845      |
|    total_timesteps  | 498280   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 1.18     |
|    n_updates        | 112069   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rat

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49900    |
|    fps              | 588      |
|    time_elapsed     | 847      |
|    total_timesteps  | 499000   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 2.92     |
|    n_updates        | 112249   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49904    |
|    fps              | 588      |
|    time_elapsed     | 847      |
|    total_timesteps  | 499040   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 1.81     |
|    n_updates        | 112259   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rat

----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49976    |
|    fps              | 588      |
|    time_elapsed     | 848      |
|    total_timesteps  | 499760   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 2.39     |
|    n_updates        | 112439   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rate | 0.05     |
| time/               |          |
|    episodes         | 49980    |
|    fps              | 588      |
|    time_elapsed     | 848      |
|    total_timesteps  | 499800   |
| train/              |          |
|    learning_rate    | 0.0001   |
|    loss             | 0.628    |
|    n_updates        | 112449   |
----------------------------------
----------------------------------
| rollout/            |          |
|    exploration_rat

## 5. Save and Reload Model

In [99]:
DQN_path = os.path.join('Training', 'Saved Models', '_DQN_Test_env9_model_50k_esp_2')

In [100]:
model.save(DQN_path)

In [101]:
DQN_path

'Training\\Saved Models\\_DQN_Test_env9_model_50k_esp_2'

## Xem log tensorborad

In [12]:
##chạy đường dẫn 
training_log_path = os.path.join(log_path, 'DQN_149')
##-> chạy cmd cd Test\Training\Logs\DQN_149 --> chạy lệnh tensorboard --logdir=. 

## 6. Evaluate and Test

In [53]:
evaluate_policy(model, env, n_eval_episodes=10)

(0.2, 2.4)

In [50]:
data = pd.read_csv("Data_test/data_demo.csv")
data_request_list = data.request.to_list()
data_response_list = data.response_simple.to_list()
data_lable_list = data.lable.to_list()
data_value_list = data._value_.to_list()

episodes = 10
for episode in range(1, episodes+1):
    obs = env.reset()
    print(f"Current State {obs}: {data_request_list[int(data_value_list.index(obs))]}")
    done = False
    total_reward = 0 
    
    print(f"========= Episode {episode} =========")
    
    while not done:
        #print(f"Current State: {obs}")
        action, _ = model.predict(obs)
        print(f"Selected Action {action}: \n{data_response_list[int(action)]}")
        
        obs, reward, done, info = env.step(action)
        
        print(f"Reward: {reward}")
        
        total_reward += reward
        print(f"\nNext State {obs}: {data_request_list[int(data_value_list.index(obs))]}")
        #break
    print(f"Total Reward for Episode {episode}: {total_reward}\n\n")

Current State [139]: ip=127.0.0.1+%26%26+whoami&Submit=Submit
========= Episode 1 =========
Selected Action [35]: 
PING 127.0.0.1 (127.0.0.1): 56 data bytes
64 bytes from 127.0.0.1: icmp_seq=0 ttl=127 time=47.872 ms
64 bytes from 127.0.0.1: icmp_seq=1 ttl=127 time=38.189 ms
64 bytes from 127.0.0.1: icmp_seq=2 ttl=127 time=37.924 ms
64 bytes from 127.0.0.1: icmp_seq=3 ttl=127 time=48.481 ms
--- 127.0.0.1 ping statistics ---
4 packets transmitted, 4 packets received, 0% packet loss
round-trip min/avg/max/stddev = 37.924/43.117/48.481/5.065 ms
www-data
Reward: [0.]

Next State [119]: ip=8.8.8.8+%7Cuname+-a&Submit=Submit
Selected Action [19]: 
Linux 858774c0c3a7 6.1.0-kali5-amd64 #1 SMP PREEMPT_DYNAMIC Debian 6.1.12-1kali2 (2023-02-23) x86_64 GNU/Linux
Reward: [0.]

Next State [199]: ?name=%3Cscript%3Ealert%28%22XSS%22%29%3B%3C%2Fscript%3E
Selected Action [99]: 
XSS
Reward: [1.]

Next State [201]: ?name=%3Cscript%3Ealert%282%29%3B%3C%2Fscript%3E
Selected Action [130]: 
Password Changed.
Re